<p style="font-family: Arial; font-size:2.75em;color:blue; font-style:bold"><br>
Projet 6 :<br><br>
Catégorisez automatiquement des questions<br><br>
</p><br>

* **Data Source / Data Source :** 
    - Data :
        - Outils d'extraction de data : https://data.stackexchange.com/stackoverflow
        - Script : https://github.com/EricJacquesPro/TextCategorization/blob/master/SQL/ExtractionDonnees.sql
    - Source Python : https://github.com/EricJacquesPro/TextCategorization
* **Description / Description : ** Projet 6 de la formation Data Scientist Proposée par OpenClassroom
    - Analyse
    - Entrainement
* **Auteur / Author : ** Eric JACQUES 
* **Date : ** 17/07/2020 

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
I - Sélection des datas entrantes</p>

Stack overfloaw met a disposition un outils en ligne permettant d'extraire le contenu de post diffusés sur le site internet.
(https://data.stackexchange.com/stackoverflow)<br>
En se basant sur la structure de la base de données(https://i.stack.imgur.com/JZHsN.png), il en ressort des données (tables) plus intéressantes que d'autres : Post, type de post, Tag, tags des posts <br>
Pour notre cas, tous les posts ne sont pas intéressants : Supprimé, score null, sans réponse, type de post....<br>
<br>
Parmis les posts, les données les plus explicites qui permettent de connaitre leurs sujets sont le body.<br>
<br>
Script téléchargeable sur https://github.com/EricJacquesPro/TextCategorization/blob/master/SQL/ExtractionDonnees.sql



<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
II - Data cleaning & preprocessing</p>

In [40]:
import sys
import os
import numpy as np
import pandas as pd
sys.path.insert(0, './Python/')

In [41]:
'''
python class for the data engineering (reading, cleaning, training...)
localised in ./Python
'''
from tagText import TagText 

In [42]:
cluster_number_min = 2
cluster_number_max = 10
cluster_number_step = 2

tagText = TagText()
print(tagText.urlDirectory)#folder for cvs file generated by SQL query (cf. I) 
print(tagText.fileName)#name of the cvs file generated by SQL query (cf. I)
tagText.nombre_post_entree = 40000
tagText.precision = 40000
data_question = tagText.read_source()
data_question.head()

Data/
QuestionVsTags.csv


Id                                               body  \
0  11227809  <p>Here is a piece of C++ code that shows some...   
1    927358  <p>I accidentally committed the wrong files to...   
2   2003505  <p>I want to delete a branch both locally and ...   
3    292357  <p>What are the differences between <code>git ...   
4    477816  <p>I've been messing around with <a href="http...   

                                               title  \
0  Why is processing a sorted array faster than p...   
1  How do I undo the most recent local commits in...   
2  How do I delete a Git branch locally and remot...   
3  What is the difference between 'git pull' and ...   
4             What is the correct JSON content type?   

                                                tags  \
0  <java><c++><performance><optimization><branch-...   
1  <git><version-control><git-commit><undo><pre-c...   
2  <git><version-control><git-branch><git-push><g...   
3        <git><version-control><git-pull><git-fetch>   
4                 <json><http-headers><content-type>   

                               SelectedTags      Name  
0        java,c++,performance,optimization,  Question  
1           git,version-control,git-commit,  Question  
2  git,version-control,git-branch,git-push,  Question  
3                      git,version-control,  Question  
4           json,http-headers,content-type,  Question

In [43]:
data_question.describe().T

count          mean           std  min        25%        50%  \
Id  40000.0  1.064466e+07  1.155872e+07  4.0  2020069.5  6185453.0   

           75%         max  
Id  15677967.0  61411498.0

In [44]:
print(tagText.stopwords)
'''Stop word issu to nltk.corpus'''

{'on', 'y', 'they', 'shan', 'she', 'both', 'mustn', 'it', 'because', 'him', 'same', 'them', 's', 'can', 'the', 'in', 'each', "should've", "won't", 'between', 'from', 'been', 'didn', 'were', 'shouldn', "mustn't", 'our', 'mightn', 'themselves', "it's", "hadn't", 'who', 'we', 'theirs', 'up', 'only', 'i', 'not', 'ours', "you've", 'does', 'you', 'nor', 'why', "she's", 'before', 'hasn', 'while', 'until', 'its', 'has', 'such', 'aren', 've', 'this', 'very', 'wouldn', 'having', 'haven', 'd', 'those', 'again', 'are', 'ain', 'wasn', 'my', 'was', 'a', 'than', "doesn't", 'yourselves', 'his', "wouldn't", "you're", 'have', 'being', 'yours', 'under', 't', 'these', 'am', 'doing', 'few', "didn't", 'as', 'needn', "couldn't", "wasn't", 'll', 'm', 'or', 'and', 'that', "weren't", 'during', 'with', 'so', 'had', 'to', 'do', 'did', 'too', 'now', 'their', 'there', 'which', 'hers', 'most', "hasn't", "don't", 'is', 'down', 'through', 'over', 'some', 're', 'itself', "mightn't", 'but', 'weren', 'once', 'ourselves',

'Stop word issu to nltk.corpus'

In [45]:
data_question['body'][1:9]

1    <p>I accidentally committed the wrong files to...
2    <p>I want to delete a branch both locally and ...
3    <p>What are the differences between <code>git ...
4    <p>I've been messing around with <a href="http...
5    <p>What is the use of the <code>yield</code> k...
6    <p>I mistakenly added files to Git using the c...
7    <p>After reading <a href="http://groups.google...
8    <p>I don't want to rename a remote branch, as ...
Name: body, dtype: object

<p style="font-family: Arial; color:red; font-style:bold">
Deleting nltk stopwords is not enough because there are lot of html and punctuation caracters
</p>

In [46]:
data_preprocessed = data_question['body'].apply(tagText.preprocessing)
print(data_preprocessed[1:9])

1    accidentally committed wrong files git pushed ...
2    want delete branch locally remotely failed att...
3                       differences git pull git fetch
4    ive messing around json time pushing text hurt...
5    use yield keyword python do example im trying ...
6    mistakenly added files git using command git a...
7    reading hidden features dark corners cstl comp...
8    want rename remote branch described rename mas...
Name: body, dtype: object


In [47]:
data_question.head()

Id                                               body  \
0  11227809  <p>Here is a piece of C++ code that shows some...   
1    927358  <p>I accidentally committed the wrong files to...   
2   2003505  <p>I want to delete a branch both locally and ...   
3    292357  <p>What are the differences between <code>git ...   
4    477816  <p>I've been messing around with <a href="http...   

                                               title  \
0  Why is processing a sorted array faster than p...   
1  How do I undo the most recent local commits in...   
2  How do I delete a Git branch locally and remot...   
3  What is the difference between 'git pull' and ...   
4             What is the correct JSON content type?   

                                                tags  \
0  <java><c++><performance><optimization><branch-...   
1  <git><version-control><git-commit><undo><pre-c...   
2  <git><version-control><git-branch><git-push><g...   
3        <git><version-control><git-pull><git-fetch>   
4                 <json><http-headers><content-type>   

                               SelectedTags      Name  
0        java,c++,performance,optimization,  Question  
1           git,version-control,git-commit,  Question  
2  git,version-control,git-branch,git-push,  Question  
3                      git,version-control,  Question  
4           json,http-headers,content-type,  Question

In [48]:
data_preprocessed.describe()

count                                                 40000
unique                                                40000
top       possible duplicate python os running on title ...
freq                                                      1
Name: body, dtype: object

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
III - Data - Bag of words</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
III.1 - Data - Bag of words - most frequent data</p>

In [49]:
import nltk
print(nltk.word_tokenize(data_preprocessed[0])[0:10])
print(nltk.tokenize.WhitespaceTokenizer().tokenize(data_preprocessed[0])[0:10])
# Tokenize using Punctuations
print(nltk.tokenize.WordPunctTokenizer().tokenize(data_preprocessed[0])[0:10])
print(nltk.tokenize.TreebankWordTokenizer().tokenize(data_preprocessed[0])[0:10])

['piece', 'c', 'code', 'shows', 'peculiar', 'behavior', 'strange', 'reason', 'sorting', 'data']
['piece', 'c', 'code', 'shows', 'peculiar', 'behavior', 'strange', 'reason', 'sorting', 'data']
['piece', 'c', 'code', 'shows', 'peculiar', 'behavior', 'strange', 'reason', 'sorting', 'data']
['piece', 'c', 'code', 'shows', 'peculiar', 'behavior', 'strange', 'reason', 'sorting', 'data']


<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
III.2 - Data - Bag of words - Nb of occurence</p>

In [50]:
import nltk
from collections import defaultdict
    
corpora = defaultdict(list)
        
tokenizer = nltk.RegexpTokenizer(r'\w+')
for id, row in data_preprocessed.iteritems():
    for word in tokenizer.tokenize(row):
        if not word in corpora :
            corpora[word] = 0
        #print(word)
        corpora[word] += 1
    

#print(corpora)
#print(sorted(corpora.items(), reverse=True,  key=lambda x: x[1]))

In [51]:
import matplotlib.pyplot as plt
minimum_count = 2#200
def count_word_occurencies(df):
        corpora = defaultdict(list)                
        tokenizer = nltk.RegexpTokenizer(r'\w+')
        for id, row in df.iteritems():
            for word in tokenizer.tokenize(row):
                if not word in corpora :
                    corpora[word] = 0
                #print(word)
                corpora[word] += 1
        corpora = dict((k, v) for k, v in corpora.items() if ((v > minimum_count)))
        sorted(corpora)
        print('''test0''')
        print(corpora)
        corpora = dict((k, v) for k, v in corpora.items() if ((v > 1)))# and (v > lower_bound) and (v < upper_bound)))
        print('''test''')
        print(corpora)
        return (sorted(corpora.items(), reverse=True,  key=lambda x: x[1]))

dico = count_word_occurencies(data_preprocessed)


In [52]:
dico = count_word_occurencies(data_preprocessed)

test0
{'versioning': 36, 'stylecop': 3, 'ngsrc': 3, 'classnavitem': 26, 'webpack': 144, 'commenter': 3, 'memberid': 7, '2d': 87, '1st': 67, '18px': 12, 'pleased': 3, 'headerview': 10, 'linqpad': 4, 'stylepadding': 5, 'consequence': 13, 'autocrlf': 3, 'thisparent': 4, 'performed': 90, 'tablecolumn': 3, 'listprice': 3, 'dateadded': 6, 'randmax': 5, 'brought': 34, 'privateval': 5, 'constants': 111, 'determined': 58, 'getinputstream': 4, 'scenegraph': 4, 'user0123456789': 5, '500f': 4, 'nsjsonserialization': 6, 'whoever': 12, 'varrundockersock': 4, 'libstdcso6': 6, 'stmtclose': 3, 'reducers': 7, 'textoverflow': 13, 'invalidateoptionsmenu': 7, 'assemblys': 16, 'cmd': 203, 'consolewritelinevalue': 4, 'testinnerhtml': 5, 'organizational': 5, 'necessarily': 99, 'scoped': 17, 'relationship': 137, 'fastest': 118, 'syslog': 13, 'praise': 3, '129': 4, 'econnreset': 10, 'mainint': 32, 'subtly': 4, 'app2': 4, 'kramer65virtualbox': 10, 'ipp': 7, 'selectedvalue': 14, 'storeid': 4, 'p5cm': 3, 'microopt

In [53]:
print(len(dico))
dico

35564


[('like', 15684),
 ('using', 14108),
 ('im', 13566),
 ('use', 12845),
 ('want', 11765),
 ('code', 11750),
 ('get', 11256),
 ('way', 11178),
 ('would', 10574),
 ('file', 10541),
 ('new', 9826),
 ('error', 9006),
 ('this', 8813),
 ('one', 8685),
 ('string', 8667),
 ('1', 8476),
 ('class', 7901),
 ('function', 7387),
 ('public', 7324),
 ('return', 7278),
 ('know', 6799),
 ('need', 6595),
 ('following', 6173),
 ('0', 6092),
 ('example', 6036),
 ('ive', 6027),
 ('something', 5930),
 ('2', 5839),
 ('it', 5804),
 ('set', 5706),
 ('data', 5605),
 ('work', 5428),
 ('id', 5415),
 ('c', 5370),
 ('method', 5351),
 ('value', 5219),
 ('var', 5171),
 ('name', 5072),
 ('find', 4886),
 ('git', 4838),
 ('trying', 4771),
 ('div', 4724),
 ('also', 4703),
 ('object', 4614),
 ('tried', 4472),
 ('could', 4463),
 ('line', 4388),
 ('int', 4327),
 ('question', 4318),
 ('files', 4309),
 ('time', 4267),
 ('type', 4260),
 ('make', 4192),
 ('run', 4140),
 ('see', 4104),
 ('list', 4075),
 ('problem', 3950),
 ('proje

In [54]:
print(tagText.count_word_occurencies(data_preprocessed))

[('like', 15684), ('using', 14108), ('im', 13566), ('use', 12845), ('want', 11765), ('code', 11750), ('get', 11256), ('way', 11178), ('would', 10574), ('file', 10541), ('new', 9826), ('error', 9006), ('this', 8813), ('one', 8685), ('string', 8667), ('1', 8476), ('class', 7901), ('function', 7387), ('public', 7324), ('return', 7278), ('know', 6799), ('need', 6595), ('following', 6173), ('0', 6092), ('example', 6036), ('ive', 6027), ('something', 5930), ('2', 5839), ('it', 5804), ('set', 5706), ('data', 5605), ('work', 5428), ('id', 5415), ('c', 5370), ('method', 5351), ('value', 5219), ('var', 5171), ('name', 5072), ('find', 4886), ('git', 4838), ('trying', 4771), ('div', 4724), ('also', 4703), ('object', 4614), ('tried', 4472), ('could', 4463), ('line', 4388), ('int', 4327), ('question', 4318), ('files', 4309), ('time', 4267), ('type', 4260), ('make', 4192), ('run', 4140), ('see', 4104), ('list', 4075), ('problem', 3950), ('project', 3872), ('two', 3852), ('user', 3845), ('3', 3829), (

<p style="font-family: Arial; color:red; font-style:bold">
Generating a dictionary of the most frequent terms is not interesting because we find a lot of words without great interest
</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
III.2 - Data - Bag of words - TF-IDF</p>

In [55]:
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import TfidfVectorizer

stemmer = nltk.stem.porter.PorterStemmer()
stopword = nltk.corpus.stopwords.words('english')

#X = data_preprocessed.unique()
X = data_preprocessed[0:9].unique()

def stem_and_filter(doc):
    tokens = [stemmer.stem(w) for w in analyzer(doc)]
    return [token for token in tokens if token.isalpha()]

analyzer = TfidfVectorizer().build_analyzer()
cv = TfidfVectorizer(lowercase=True, stop_words="english", analyzer=stem_and_filter, min_df=0.00, max_df=0.3)  # we remove words if it appears in more than 30 % of the corpus (not found stopwords like Box, Christmas and so on)
word_count_vector = cv.fit_transform(X)
print("TF_IDF_matrix :", word_count_vector.shape, "of", word_count_vector.dtype)
tfidf_transformer=TfidfTransformer(smooth_idf=True,use_idf=True)
tfidf_transformer.fit(word_count_vector)
# print idf values
df_idf = pd.DataFrame(tfidf_transformer.idf_, index=cv.get_feature_names(),columns=["tf_idf_weights"])
 
# sort ascending
df_idf.sort_values(by=['tf_idf_weights'])


TF_IDF_matrix : (9, 247) of float64


tf_idf_weights
file                              2.203973
time                              2.203973
int                               2.203973
branch                            2.203973
start                             2.203973
thi                               2.203973
return                            2.203973
tri                               2.203973
piec                              2.203973
repositori                        2.203973
id                                2.203973
pull                              2.203973
remot                             2.203973
commit                            2.203973
compil                            2.203973
result                            2.203973
standard                          2.203973
differ                            2.203973
undo                              2.203973
similar                           2.203973
yet                               2.203973
well                              2.203973
want                              2.203973
new                               2.203973
complet                           2.203973
main                              2.203973
run                               2.203973
use                               2.203973
selfmedian                        2.609438
read                              2.609438
...                                    ...
iostream                          2.609438
initi                             2.609438
exampl                            2.609438
extrem                            2.609438
fail                              2.609438
faster                            2.609438
featur                            2.609438
fetch                             2.609438
first                             2.609438
follow                            2.609438
found                             2.609438
from                              2.609438
gather                            2.609438
gcc                               2.609438
intarrays                         2.609438
gener                             2.609438
getchildcandidatesself            2.609438
githubcomgitusergitproject        2.609438
go                                2.609438
goe                               2.609438
great                             2.609438
happen                            2.609438
here                              2.609438
hidden                            2.609438
hurt                              2.609438
im                                2.609438
import                            2.609438
independ                          2.609438
getchildcandid                    2.609438
yield                             2.609438

[247 rows x 1 columns]

<p style="font-family: Arial; color:red; font-style:bold">
The words proposed following the TF-IDF generation seem more interesting than the list of the most frequent words.
We will favor TF-IDF for the rest.
</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV - Data - Tag genetaor </p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV.1 - Data - Tag generator - Unsupervised - By nb of occurence</p>

In [56]:
dict_tag = count_word_occurencies(data_preprocessed)
dict_tag = str(dict_tag)
dict_tag


test0
{'versioning': 36, 'stylecop': 3, 'ngsrc': 3, 'classnavitem': 26, 'webpack': 144, 'commenter': 3, 'memberid': 7, '2d': 87, '1st': 67, '18px': 12, 'pleased': 3, 'headerview': 10, 'linqpad': 4, 'stylepadding': 5, 'consequence': 13, 'autocrlf': 3, 'thisparent': 4, 'performed': 90, 'tablecolumn': 3, 'listprice': 3, 'dateadded': 6, 'randmax': 5, 'brought': 34, 'privateval': 5, 'constants': 111, 'determined': 58, 'getinputstream': 4, 'scenegraph': 4, 'user0123456789': 5, '500f': 4, 'nsjsonserialization': 6, 'whoever': 12, 'varrundockersock': 4, 'libstdcso6': 6, 'stmtclose': 3, 'reducers': 7, 'textoverflow': 13, 'invalidateoptionsmenu': 7, 'assemblys': 16, 'cmd': 203, 'consolewritelinevalue': 4, 'testinnerhtml': 5, 'organizational': 5, 'necessarily': 99, 'scoped': 17, 'relationship': 137, 'fastest': 118, 'syslog': 13, 'praise': 3, '129': 4, 'econnreset': 10, 'mainint': 32, 'subtly': 4, 'app2': 4, 'kramer65virtualbox': 10, 'ipp': 7, 'selectedvalue': 14, 'storeid': 4, 'p5cm': 3, 'microopt

"[('like', 15684), ('using', 14108), ('im', 13566), ('use', 12845), ('want', 11765), ('code', 11750), ('get', 11256), ('way', 11178), ('would', 10574), ('file', 10541), ('new', 9826), ('error', 9006), ('this', 8813), ('one', 8685), ('string', 8667), ('1', 8476), ('class', 7901), ('function', 7387), ('public', 7324), ('return', 7278), ('know', 6799), ('need', 6595), ('following', 6173), ('0', 6092), ('example', 6036), ('ive', 6027), ('something', 5930), ('2', 5839), ('it', 5804), ('set', 5706), ('data', 5605), ('work', 5428), ('id', 5415), ('c', 5370), ('method', 5351), ('value', 5219), ('var', 5171), ('name', 5072), ('find', 4886), ('git', 4838), ('trying', 4771), ('div', 4724), ('also', 4703), ('object', 4614), ('tried', 4472), ('could', 4463), ('line', 4388), ('int', 4327), ('question', 4318), ('files', 4309), ('time', 4267), ('type', 4260), ('make', 4192), ('run', 4140), ('see', 4104), ('list', 4075), ('problem', 3950), ('project', 3872), ('two', 3852), ('user', 3845), ('3', 3829), 

In [57]:
def unsupervised_tag(dict_word_key, new_question, number_max_tag):
    tags = [word for word in new_question.split() if (word in dict_word_key)]
    return tags[0:number_max_tag]

print(unsupervised_tag(dict_tag, "How save my code source with soft like git", 20))
print(unsupervised_tag(dict_tag, "How save my code source with soft like like git", 2))

['save', 'my', 'code', 'source', 'with', 'soft', 'like', 'git']
['save', 'my']


In [58]:
tagText.unsupervised_tag(dict_tag, "How save my code source with soft like git", 2)

['save', 'my']

<p style="font-family: Arial; color:red; font-style:bold">
Not interesting because we receive words without interest
</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV.2-a - Data - Tag generator - Unsupervised - LDA</p>

<p style="font-family: Arial; color:red; font-style:bold">
For more detals about LDA and to generate lda.joblib, please, see the notebook Projet_V2_LDA-v2-Detals.ipynb
</p>

In [59]:
'''
If you want to load lda model generated in the other notebook
'''
from joblib import dump, load
lda_load = load('lda.joblib') 
df_topic_keywords_load = load('df_lda_topic_keywords.joblib') 
tf_vectorizer_load = load('tf_lda_vectorizer.joblib')

print(lda_load)

LatentDirichletAllocation(batch_size=128, doc_topic_prior=None,
             evaluate_every=-1, learning_decay=0.7,
             learning_method='online', learning_offset=10.0,
             max_doc_update_iter=100, max_iter=10, mean_change_tol=0.001,
             n_components=10, n_jobs=-1, n_topics=32, perp_tol=0.1,
             random_state=100, topic_word_prior=None,
             total_samples=1000000.0, verbose=0)


In [60]:
'''
If you want to generate lda model
'''
lda_load, df_topic_keywords_load, tf_vectorizer_load = tagText.lda_prepare_tag(data_preprocessed, 32)


C:\Users\naru_\Anaconda3\lib\site-packages\sklearn\decomposition\online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)


{'doc_topic_prior': None, 'evaluate_every': -1, 'random_state': 100, 'n_topics': 32, 'max_iter': 10, 'learning_decay': 0.7, 'learning_offset': 10.0, 'topic_word_prior': None, 'learning_method': 'online', 'max_doc_update_iter': 100, 'total_samples': 1000000.0, 'verbose': 0, 'n_jobs': -1, 'mean_change_tol': 0.001, 'perp_tol': 0.1, 'n_components': 10, 'batch_size': 128}
Log Likelihood:  -14449771.6389
Perplexity:  6502.42160448
{'doc_topic_prior': None, 'evaluate_every': -1, 'random_state': 100, 'n_topics': 32, 'max_iter': 10, 'learning_decay': 0.7, 'learning_offset': 10.0, 'topic_word_prior': None, 'learning_method': 'online', 'max_doc_update_iter': 100, 'total_samples': 1000000.0, 'verbose': 0, 'n_jobs': -1, 'mean_change_tol': 0.001, 'perp_tol': 0.1, 'n_components': 10, 'batch_size': 128}


In [61]:

print('Topics From working class : ')
tagText.display_topics(lda_load, tf_vectorizer_load.get_feature_names(), 10)


Topics From working class : 
Topic : 0 :
java interface implementation template map struct 30 suppose frame abstract
Topic : 1 :
question way like ive answer option solution code set use
Topic : 2 :
class public import void view new private static method foo
Topic : 3 :
project default date time button set info tag action place
Topic : 4 :
use difference php used field similar case type vs using
Topic : 5 :
page jquery javascript load fragment session login ajax domain redirect
Topic : 6 :
im like using want file use way tried work need
Topic : 7 :
server build app thing message web run running using client
Topic : 8 :
html os ruby rails passed properties gem happen intent utf8
Topic : 9 :
table select data database query id sql column mysql null
Topic : 10 :
function code data use type method return like using request
Topic : 11 :
string return var value object like array new way want
Topic : 12 :
application script path echo 10 bash file 11 process enum
Topic : 13 :
right left join s

In [62]:
print(tagText.lda_predict( "How to cast number as integer in java", lda_load, df_topic_keywords_load, tf_vectorizer_load, 5))

int code compile long include


<p style="font-family: Arial; color:red; font-style:bold">
LDA prediction seems to be interesting
</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV.2-b - Data - Tag generator - Unsupervised - MNF</p>

In [63]:
nmf_tagText, df_nmf_topic_keywords, tf_mnf_vectorizer = tagText.nmf_prepare_tag(data_preprocessed, 32)
            
tagText.nmf_predict('git est un outils de code source.', nmf_tagText, df_nmf_topic_keywords, tf_mnf_vectorizer, 5)

original reconstruction error automatically calculated -> TRAIN:  191.452972342
Manually calculated rec-error train:  191.452976384


'git commit repository push changes'

In [64]:
from joblib import dump, load
dump(nmf_tagText, 'nmf.joblib') 
dump(df_nmf_topic_keywords, 'df_nmf_topic_keywords.joblib') 
dump(tf_mnf_vectorizer, 'tf_mnf_vectorizer.joblib') 

nmfLoad = load('nmf.joblib') 
print(nmfLoad)

NMF(alpha=0.1, beta_loss='frobenius', init='nndsvd', l1_ratio=0.5,
  max_iter=200, n_components=32, random_state=1, shuffle=False,
  solver='cd', tol=0.0001, verbose=0)


In [65]:
lda_tagText, df_lda_topic_keywords, tf_lda_vectorizer = tagText.lda_prepare_tag_and_save(data_preprocessed)
mnf_tagText, df_nmf_topic_keywords, tf_mnf_vectorizer = tagText.nmf_prepare_tag_and_save(data_preprocessed)

print(tagText.lda_predict('git est un outils de code source. C\'est bien', lda_tagText, df_lda_topic_keywords, tf_lda_vectorizer, 5))
print(tagText.nmf_predict('git est un outils de code source. C\'est bien', mnf_tagText, df_nmf_topic_keywords, tf_mnf_vectorizer, 5))


C:\Users\naru_\Anaconda3\lib\site-packages\sklearn\decomposition\online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)


{'doc_topic_prior': None, 'evaluate_every': -1, 'random_state': 100, 'n_topics': 32, 'max_iter': 10, 'learning_decay': 0.7, 'learning_offset': 10.0, 'topic_word_prior': None, 'learning_method': 'online', 'max_doc_update_iter': 100, 'total_samples': 1000000.0, 'verbose': 0, 'n_jobs': -1, 'mean_change_tol': 0.001, 'perp_tol': 0.1, 'n_components': 10, 'batch_size': 128}
Log Likelihood:  -14449720.2712
Perplexity:  6502.21865484
{'doc_topic_prior': None, 'evaluate_every': -1, 'random_state': 100, 'n_topics': 32, 'max_iter': 10, 'learning_decay': 0.7, 'learning_offset': 10.0, 'topic_word_prior': None, 'learning_method': 'online', 'max_doc_update_iter': 100, 'total_samples': 1000000.0, 'verbose': 0, 'n_jobs': -1, 'mean_change_tol': 0.001, 'perp_tol': 0.1, 'n_components': 10, 'batch_size': 128}
original reconstruction error automatically calculated -> TRAIN:  191.452972342
Manually calculated rec-error train:  191.452976384
component react dev ex modal
git commit repository push changes


<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV.3 - Data - Tag generator - Supervised</p>

In [66]:
classifier, tags = tagText.supervised_prepare_tag(data_preprocessed, data_question['SelectedTags'])
message = 'git est un outils de code source. C\'est bien'

print(message)

print(tagText.supervised_predict(message, classifier, tags))

git est un outils de code source. C'est bien
['android', 'c#', 'java', 'javascript', 'python']


In [67]:
print(tagText.supervised_predict(data_preprocessed[0], classifier, tags ))

['android', 'c#', 'java', 'javascript', 'python']


<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
V - Resultat</p>

In [68]:

import numpy as np
import nltk
import pandas as pd
import os
import sys

sys.path.insert(0, './Python/')

from tagText import TagText


tagText = TagText()
print(tagText.urlDirectory)
print(tagText.fileName)
nombre_post_entree = 40000
precision = 40000
tagText.nombre_post_entree = nombre_post_entree
tagText.precision = precision
nombre_suggestion = 5

def supervisedTagPurposer():
    return tagPurposer('supervised', 'This is a test to have tag GIT & branche', 'false', 'false')

def supervisedTagPurposerAndReload():
    return tagPurposer('supervised', 'This is a test to have tag GIT & branche', 'true', 'false')

def supervisedTagPurposerAndReloadAndSave():
    return tagPurposer('supervised', 'This is a test to have tag GIT & branche', 'true', 'true')

def tagLDAPurposer():
    return tagPurposer('LDA', 'This is a test to have tag GIT & branche', 'false', 'false')

def tagLDAPurposerAndReload():
    return tagPurposer('LDA', 'This is a test to have tag GIT & branche', 'true', 'false')

def tagLDAPurposerAndReloadAndSave():
    return tagPurposer('LDA', 'This is a test to have tag GIT & branche', 'true', 'true')

def tagNMFPurposer():
    return tagPurposer('NMF', 'This is a test to have tag GIT & branche', 'false', 'false')

def tagNMFPurposerAndReload():
    return tagPurposer('NMF', 'This is a test to have tag GIT & branche', 'true', 'false')

def tagNMFPurposerAndReloadAndSave():
    return tagPurposer('NMF', 'This is a test to have tag GIT & branche', 'true', 'true')

def tagPurposer(mode, message, reload, saveModel):
    if mode.lower() == 'supervised':
        return superviedTagPurposerFromMessage(message, reload.lower(), saveModel.lower())
    if mode.lower() == 'lda' or mode.lower() =='nmf':
        return unsuperviedTagTFIDFPurposerFromMessage(mode.lower(), message, reload.lower(), saveModel.lower())
    return '/i\\Mode indefined/i\\'

def superviedTagPurposerFromMessage(message, reload, saveModel):
    tagText = TagText()
    tagText.nombre_post_entree = nombre_post_entree
    tagText.precision = precision
    tags = ''
    if reload.lower() == 'true':
        data_question = tagText.read_source()
        data_preprocessed = data_question['body'].apply(tagText.preprocessing)
        if saveModel.lower() == 'true':
            classifier, tags_existants = tagText.supervised_prepare_tag_and_save(data_preprocessed, data_question['SelectedTags'])
            tags = tagText.supervised_predict(message, classifier, tags_existants)
        else :
            classifier, tags_existants = tagText.supervised_prepare_tag(data_preprocessed, data_question['SelectedTags'])
            tags = tagText.supervised_predict(message, classifier, tags_existants)
    else:
        classifier, tags_existants = tagText.supervised_prepare_tag_load()
        tags = tagText.supervised_predict(message, classifier, tags_existants)
    return tags

def unsuperviedTagTFIDFPurposerFromMessage(option, message, reloadModel, saveModel):
    tagText = TagText()
    tagText.nombre_post_entree = nombre_post_entree
    tagText.precision = precision
    tags = ''
    if option.lower() != 'lda' and option.lower() != 'nmf':
        return '/i\\Mode indefined/i\\'
    if reloadModel.lower() == 'true':
        data_question = tagText.read_source()
        data_preprocessed = data_question['body'].apply(tagText.preprocessing)
        if option.lower() == 'lda':
            if saveModel.lower() == 'true':
                lda_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText = tagText.lda_prepare_tag_and_save(data_preprocessed)
                tags = tagText.lda_predict(message, lda_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText, nombre_suggestion)
            else:
                lda_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText = tagText.lda_prepare_tag(data_preprocessed)
                tags = tagText.lda_predict(message, lda_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText, nombre_suggestion)
        if option.lower() == 'nmf':
            if saveModel.lower() == 'true':
                nmf_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText = tagText.nmf_prepare_tag_and_save(data_preprocessed)
                tags = tagText.nmf_predict(message, nmf_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText, nombre_suggestion)
            else:
                nmf_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText = tagText.nmf_prepare_tag(data_preprocessed)
                tags = tagText.nmf_predict(message, nmf_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText, nombre_suggestion)
    else:
        if option.lower() == 'lda':
            lda_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText = tagText.lda_prepare_tag_load()
            tags = tagText.lda_predict(message, lda_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText, nombre_suggestion)
        if option.lower() == 'nmf':
            nmf_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText = tagText.nmf_prepare_tag_load()
            tags = tagText.nmf_predict(message, nmf_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText, nombre_suggestion)
    return tags


Data/
QuestionVsTags.csv


In [69]:
tagLDAPurposerAndReloadAndSave()

C:\Users\naru_\Anaconda3\lib\site-packages\sklearn\decomposition\online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)


{'doc_topic_prior': None, 'evaluate_every': -1, 'random_state': 100, 'n_topics': 32, 'max_iter': 10, 'learning_decay': 0.7, 'learning_offset': 10.0, 'topic_word_prior': None, 'learning_method': 'online', 'max_doc_update_iter': 100, 'total_samples': 1000000.0, 'verbose': 0, 'n_jobs': -1, 'mean_change_tol': 0.001, 'perp_tol': 0.1, 'n_components': 10, 'batch_size': 128}
Log Likelihood:  -14449754.1058
Perplexity:  6502.35233212
{'doc_topic_prior': None, 'evaluate_every': -1, 'random_state': 100, 'n_topics': 32, 'max_iter': 10, 'learning_decay': 0.7, 'learning_offset': 10.0, 'topic_word_prior': None, 'learning_method': 'online', 'max_doc_update_iter': 100, 'total_samples': 1000000.0, 'verbose': 0, 'n_jobs': -1, 'mean_change_tol': 0.001, 'perp_tol': 0.1, 'n_components': 10, 'batch_size': 128}


'test json api format title'

Une API :  https://ejacques.pythonanywhere.com/apiTagGenerator/

Un depot GIT : https://github.com/EricJacquesPro/TextCategorization/

In [70]:
supervisedTagPurposerAndReload()

"['android', 'c#', 'git', 'java', 'javascript', 'python']"

In [71]:
supervisedTagPurposerAndReloadAndSave()

"['android', 'c#', 'java', 'javascript', 'python']"

In [72]:
supervisedTagPurposer()

"['android', 'c#', 'java', 'javascript', 'python']"

In [73]:
tagLDAPurposerAndReload()

C:\Users\naru_\Anaconda3\lib\site-packages\sklearn\decomposition\online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)


{'doc_topic_prior': None, 'evaluate_every': -1, 'random_state': 100, 'n_topics': 32, 'max_iter': 10, 'learning_decay': 0.7, 'learning_offset': 10.0, 'topic_word_prior': None, 'learning_method': 'online', 'max_doc_update_iter': 100, 'total_samples': 1000000.0, 'verbose': 0, 'n_jobs': -1, 'mean_change_tol': 0.001, 'perp_tol': 0.1, 'n_components': 10, 'batch_size': 128}
Log Likelihood:  -14449761.1148
Perplexity:  6502.38002437
{'doc_topic_prior': None, 'evaluate_every': -1, 'random_state': 100, 'n_topics': 32, 'max_iter': 10, 'learning_decay': 0.7, 'learning_offset': 10.0, 'topic_word_prior': None, 'learning_method': 'online', 'max_doc_update_iter': 100, 'total_samples': 1000000.0, 'verbose': 0, 'n_jobs': -1, 'mean_change_tol': 0.001, 'perp_tol': 0.1, 'n_components': 10, 'batch_size': 128}


'test json api format title'

In [74]:
tagLDAPurposerAndReloadAndSave()

C:\Users\naru_\Anaconda3\lib\site-packages\sklearn\decomposition\online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)


{'doc_topic_prior': None, 'evaluate_every': -1, 'random_state': 100, 'n_topics': 32, 'max_iter': 10, 'learning_decay': 0.7, 'learning_offset': 10.0, 'topic_word_prior': None, 'learning_method': 'online', 'max_doc_update_iter': 100, 'total_samples': 1000000.0, 'verbose': 0, 'n_jobs': -1, 'mean_change_tol': 0.001, 'perp_tol': 0.1, 'n_components': 10, 'batch_size': 128}
Log Likelihood:  -14449761.1148
Perplexity:  6502.38002437
{'doc_topic_prior': None, 'evaluate_every': -1, 'random_state': 100, 'n_topics': 32, 'max_iter': 10, 'learning_decay': 0.7, 'learning_offset': 10.0, 'topic_word_prior': None, 'learning_method': 'online', 'max_doc_update_iter': 100, 'total_samples': 1000000.0, 'verbose': 0, 'n_jobs': -1, 'mean_change_tol': 0.001, 'perp_tol': 0.1, 'n_components': 10, 'batch_size': 128}


'test json api format title'

In [75]:
tagLDAPurposer()

'test json api format title'

In [76]:
tagNMFPurposerAndReload()

original reconstruction error automatically calculated -> TRAIN:  191.452972342
Manually calculated rec-error train:  191.452976384


'git commit repository push changes'

In [77]:
tagNMFPurposerAndReloadAndSave()

original reconstruction error automatically calculated -> TRAIN:  191.452972342
Manually calculated rec-error train:  191.452976384


'git commit repository push changes'

In [78]:
tagNMFPurposer()

'git commit repository push changes'